In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


Install Required Libraries
Run this cell to install the necessary packages. CLIP requires PyTorch, and we'll use scikit-learn for clustering, along with Pillow for image loading and matplotlib for visualization.

In [ ]:
#@markdown Unzip training data from drive to /content/ (if required)
path = '/content/drive/MyDrive/training_data_91472.zip' #@param {type:'string'}

%cd /content/
!unzip  {path}

In [ ]:
!pip install ftfy regex tqdm
!pip install git+https://github.com/openai/CLIP.git
!pip install scikit-learn matplotlib pillow umap-learn  # UMAP is optional for 2D visualization

Load Images and Extract CLIP Embeddings

Upload your images the normal way ( `/content/`) prior to running this cell.

This code loads all images (supports JPG, PNG, etc.), preprocesses them, and extracts 512-dimensional embeddings using the ViT-B/32 CLIP model.

In [ ]:
!pip install open_clip_torch

import os
import numpy as np
import torch
import open_clip
from PIL import Image

# Configuration
image_dir = '/content/'  # Update this path
device = "cuda" if torch.cuda.is_available() else "cpu"
model_name = "ViT-B-32"  # Available per error message
pretrained = "laion400m_e32"  # Robust pretrained weights

# Load OpenCLIP model
model, _, preprocess = open_clip.create_model_and_transforms(model_name, pretrained=pretrained)
model.to(device)
model.eval()

# Load images and extract embeddings
embeddings = []
image_paths = []
image_names = []

# Recursively find images in subdirectories
for root, _, files in os.walk(image_dir):
    for filename in files:
        if filename.lower().endswith(('.png', '.jpg', '.jpeg', '.gif', '.bmp')):
            img_path = os.path.join(root, filename)
            try:
                image = preprocess(Image.open(img_path)).unsqueeze(0).to(device)
                with torch.no_grad():
                    embedding = model.encode_image(image)
                embeddings.append(embedding.cpu().numpy().flatten())
                image_paths.append(img_path)
                image_names.append(filename)
                print(f"Processed: {filename}")
            except Exception as e:
                print(f"Error processing {filename}: {e}")

embeddings = np.array(embeddings)
print(f"Extracted embeddings for {len(embeddings)} images. Shape: {embeddings.shape}")

Perform Clustering
We'll use K-Means clustering on the embeddings. You can choose the number of clusters (`n_clusters`) based on your dataset size (e.g., try 5-10). We'll also compute the silhouette score to evaluate cluster quality (higher is better).

For visualization, we'll optionally reduce dimensions to 2D using UMAP.

In [ ]:
from umap import UMAP  # For 2D projection (optional)
import os
import numpy as np
import torch
import clip
from PIL import Image
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import warnings
warnings.filterwarnings('ignore')
#@markdown Choose number of clusters (experiment with this)
n_clusters = 50  # @param {type:'slider' , min:1 , max:200, step:1}

# Perform K-Means clustering
kmeans = KMeans(n_clusters=n_clusters, random_state=42, n_init=10)
cluster_labels = kmeans.fit_predict(embeddings)

# Evaluate clustering quality
sil_score = silhouette_score(embeddings, cluster_labels)
print(f"Silhouette Score: {sil_score:.3f} (closer to 1 is better)")

# Optional: 2D visualization with UMAP
reducer = UMAP(random_state=42, n_components=2)
embed_2d = reducer.fit_transform(embeddings)

plt.figure(figsize=(10, 8))
scatter = plt.scatter(embed_2d[:, 0], embed_2d[:, 1], c=cluster_labels, cmap='tab10', s=50)
plt.colorbar(scatter)
plt.title(f'2D UMAP Projection of CLIP Embeddings (K={n_clusters} Clusters)')
plt.xlabel('UMAP 1')
plt.ylabel('UMAP 2')
plt.show()

In [ ]:
import shutil
import os
from PIL import Image

# Create output directories
output_dir = '/content/clusters'  # Output base directory
os.makedirs(output_dir, exist_ok=True)

move_files = False  # Set to True to move files, False to copy

# Create directories for each cluster
for i in range(n_clusters):
    cluster_dir = os.path.join(output_dir, f'cluster_{i}')
    os.makedirs(cluster_dir, exist_ok=True)

# Form inputs using Colab's # @param
output_format = "JPEG"  # @param ["JPEG", "PNG", "WEBP"]
quality = 100  # @param {type:"slider", min:0, max:100, step:1}

# Function to convert and save images
for idx, label in enumerate(cluster_labels):
    src_path = image_paths[idx]  # Use full path
    # Create destination filename with selected extension
    dst_filename = os.path.splitext(image_names[idx])[0] + f'.{output_format.lower()}'
    dst_path = os.path.join(output_dir, f'cluster_{label}', dst_filename)

    try:
        # Open and convert image
        with Image.open(src_path).convert('RGB') as img:
            if output_format == 'JPEG':
                img.save(dst_path, 'JPEG', quality=quality, optimize=True)
            elif output_format == 'PNG':
                # PNG compression: 0 (max compression) to 9 (no compression)
                # Map quality 0-100 to PNG compression 9-0
                png_compression = int(9 - (quality / 100 * 9))
                img.save(dst_path, 'PNG', compress_level=png_compression)
            elif output_format == 'WEBP':
                img.save(dst_path, 'WEBP', quality=quality)

            if move_files:
                os.remove(src_path)  # Delete original if moving
            print(f"Assigned {image_names[idx]} as {dst_filename} to cluster_{label}")
    except Exception as e:
        print(f"Error converting {image_names[idx]} to {output_format}: {e}")

print(f"Images sorted into {n_clusters} clusters in '{output_dir}' as .{output_format.lower()}")

In [ ]:
from PIL import Image
import matplotlib.pyplot as plt
import os

def display_cluster_samples(cluster_dir, n_samples=3):
    # Check if cluster directory exists
    if not os.path.exists(cluster_dir):
        print(f"Cluster directory {cluster_dir} does not exist")
        return

    # Updated to include .jpg, .png, and .webp files
    images = [f for f in os.listdir(cluster_dir) if f.lower().endswith(('.jpg', '.jpeg', '.png', '.webp'))][:n_samples]
    if not images:
        print(f"No images in {cluster_dir}")
        return

    fig, axs = plt.subplots(1, len(images), figsize=(5 * len(images), 5))
    if len(images) == 1:
        axs = [axs]
    for j, img_file in enumerate(images):
        img_path = os.path.join(cluster_dir, img_file)
        try:
            img = Image.open(img_path).convert('RGB')  # Ensure RGB for display
            axs[j].imshow(img)
            axs[j].set_title(img_file)
            axs[j].axis('off')
        except Exception as e:
            print(f"Error displaying {img_file}: {e}")
    plt.show()

# Create output directories
output_dir = '/content/clusters'  # Output base directory

# Check if output directory exists
if not os.path.exists(output_dir):
    print(f"Output directory {output_dir} does not exist")
else:
    # Display samples from each cluster
    for i in range(n_clusters):  # Ensure n_clusters is defined
        cluster_dir = os.path.join(output_dir, f'cluster_{i}')
        print(f"\nSamples from Cluster {i}:")
        display_cluster_samples(cluster_dir)

In [ ]:
import shutil
%cd /content/
#@markdown Remove folderns with junk items
nums =''#@param {type:'string'}

for num in nums.split(','):
  if num.strip() == '': continue
  shutil.rmtree(f'/content/clusters/cluster_{num.strip()}')

Sort Images into Clusters
This creates subdirectories for each cluster and moves/copies the images there. Set `move_files=True` to move (or False to copy).

Visualize Sample Images per Cluster
Display a few sample images from each cluster to inspect the results.

In [ ]:
#@markdown Upload to Google Drive as .zip folder (Be mindful of Google Drive Terms of Service)
drive_folder_name = 'mia_clusters' # @param {type:'string'}

%cd /content/
!zip -r /content/drive/MyDrive/{drive_folder_name}.zip {output_dir}

